# GymAlly Demo

## Install libraries

In [1]:
!pip install --upgrade --q google-cloud-aiplatform

## Import packages

In [46]:
import base64
import vertexai
from vertexai.generative_models import GenerativeModel, Part, FinishReason
import vertexai.preview.generative_models as generative_models
from IPython.display import HTML
from google.cloud import storage

## Define helper functions

In [4]:
# Available Gemini models
gemini_latest = "gemini-1.5-pro-latest" # Latest version, only for testing or prototyping
gemini_latest_stable = "gemini-1.5-pro" # Latest stable version, ready for prod
gemini_flash_latest_stable = "gemini-1.5-flash"

In [90]:
def load_video_part(uri):
    """Loads a video from a URI and creates a corresponding Part object.
    Args:
        uri (str): The URI of the video.
    Returns:
        Part: The loaded video as a Part object.
    """
    file_extension = uri.split('.')[-1]  # Get the file extension

    if file_extension == 'mov':
        mime_type = "video/quicktime"
    elif file_extension == 'mp4':
        mime_type = "video/mp4"
    else:
        raise ValueError("Unsupported video format. Only .mov and .mp4 are currently supported.")

    return Part.from_uri(mime_type=mime_type, uri=uri)

def generate():
    vertexai.init(project="gymally-test", location="europe-west4")
    model = GenerativeModel(gemini_latest_stable)
    responses = model.generate_content(
        ["""
        You're an AI Coach, an AI-based software that gives corrections or suggestions on how a user performs a strength exercise.,
        Given this reference video that gives corrections, tips, and common pitfalls on this exercise:""",
        ref_video, 
        """
        How good is the following user doing the exercise?""", 
        user_video,
        """
        In a friendly and motivational way, you should give a score and suggest improvements to the user as precisely as posibble
        Score is a % don't be afraid if user does it perfect to give a 100%, and improvements suggestions should include degrees info if available.
        Both score and improvements should be in a bullet-point list, split in each of the following categories: 1. Form, 2. Range of Movement, 3. Tempo.
        Besides that, if you're capable to see it in the video, estimate the total weight the user lifted. Otherwise ignore this last point.
        """],
        generation_config=generation_config,
        safety_settings=safety_settings,
        stream=True,
    )

    for response in responses:
        print(response.text, end="")


generation_config = {
    "max_output_tokens": 8192,
    "temperature": 0.5,
    "top_p": 0.95,
}

# Medium-bar safety filters
#safety_settingsgs = {
#    generative_models.HarmCategory.HARM_CATEGORY_HATE_SPEECH: generative_models.HarmBlockThreshold.BLOCK_MEDIUM_AND_ABOVE,
#    generative_models.HarmCategory.HARM_CATEGORY_DANGEROUS_CONTENT: generative_models.HarmBlockThreshold.BLOCK_MEDIUM_AND_ABOVE,
#    generative_models.HarmCategory.HARM_CATEGORY_SEXUALLY_EXPLICIT: generative_models.HarmBlockThreshold.BLOCK_MEDIUM_AND_ABOVE,
#    generative_models.HarmCategory.HARM_CATEGORY_HARASSMENT: generative_models.HarmBlockThreshold.BLOCK_MEDIUM_AND_ABOVE,
#}

# Low-bar safety filters
safety_settings = {
    generative_models.HarmCategory.HARM_CATEGORY_HATE_SPEECH: generative_models.HarmBlockThreshold.BLOCK_ONLY_HIGH,
    generative_models.HarmCategory.HARM_CATEGORY_DANGEROUS_CONTENT: generative_models.HarmBlockThreshold.BLOCK_ONLY_HIGH,
    generative_models.HarmCategory.HARM_CATEGORY_SEXUALLY_EXPLICIT: generative_models.HarmBlockThreshold.BLOCK_ONLY_HIGH,
    generative_models.HarmCategory.HARM_CATEGORY_HARASSMENT: generative_models.HarmBlockThreshold.BLOCK_ONLY_HIGH,
}


def display_video_from_gcs(uri):
    """Displays a video directly from Google Cloud Storage in a Jupyter Notebook.

    Args:
        uri (str): The GCS URI of the video (e.g., "gs://your-bucket-name/your-video-file.mp4").
    """

    storage_client = storage.Client()
    bucket_name = uri.split("/")[2]
    object_name = "/".join(uri.split("/")[3:])
    bucket = storage_client.bucket(bucket_name)
    blob = bucket.blob(object_name)

    video_bytes = blob.download_as_bytes()
    file_extension = object_name.split(".")[-1]

    base64_video = base64.b64encode(video_bytes).decode('utf-8')

    video_tag = f'<video width="640" height="480" controls><source src="data:video/{file_extension};base64,{base64_video}" type="video/{file_extension}"></video>'
    display(HTML(video_tag))
    
def display_videos_from_gcs(uri1, uri2):
    """Displays two videos side-by-side directly from Google Cloud Storage in a Jupyter Notebook.

    Args:
        uri1 (str): The GCS URI of the first video.
        uri2 (str): The GCS URI of the second video.
    """
    
    # Helper function to load a single video
    def load_video(uri):
        storage_client = storage.Client()
        bucket_name = uri.split("/")[2]
        object_name = "/".join(uri.split("/")[3:])
        bucket = storage_client.bucket(bucket_name)
        blob = bucket.blob(object_name)
        video_bytes = blob.download_as_bytes()
        file_extension = object_name.split(".")[-1]
        base64_video = base64.b64encode(video_bytes).decode('utf-8')
        return f'<video width="320" height="240" controls><source src="data:video/{file_extension};base64,{base64_video}" type="video/{file_extension}"></video>'

    # Load both videos
    video_tag1 = load_video(uri1)
    video_tag2 = load_video(uri2)
    
    # Create HTML to display videos side by side
    display(HTML(f'''
        <div style="display: flex; justify-content: space-around;">
            {video_tag1}
            {video_tag2}
        </div>
    '''))

## Load videos

In [91]:
# GCS URIs:

abduction_usr1_20240523_1_uri = "gs://gymally-mvp/exercises-videos/abduction-usr1-20240523-1.mp4"
abduction_usr1_20240527_1_uri = "gs://gymally-mvp/exercises-videos/abduction-usr1-20240527-1.mp4"
abduction_usr1_20240527_2_uri = "gs://gymally-mvp/exercises-videos/abduction-usr1-20240527-2.mp4"
abduction_usr2_20240527_1_uri = "gs://gymally-mvp/exercises-videos/abduction-usr2-20240527-1.mp4"
bench_press_ref_uri = "gs://gymally-mvp/exercises-videos/bench-press-ref.mov"
bench_press_usr3_20220501_1_uri = "gs://gymally-mvp/exercises-videos/bench-press-usr3-20220501-ex1.mp4"
bench_press_usr4_20240527_1_uri = "gs://gymally-mvp/exercises-videos/bench-press-usr4-20240527-1.mp4"
bench_press_usr4_20240527_2_uri = "gs://gymally-mvp/exercises-videos/bench-press-usr4-20240527-2.mp4"
hip_thrust_ref_uri = "gs://gymally-mvp/exercises-videos/hip-thrust-ref.mov"
hip_thrust_usr1_20240501_1_uri = "gs://gymally-mvp/exercises-videos/hip-thrust-usr1-20240501-1.mp4"
hip_thrust_usr1_20240516_1_uri = "gs://gymally-mvp/exercises-videos/hip-thrust-usr1-20240516-1.mp4"
hip_thrust_usr1_20240523_1_uri = "gs://gymally-mvp/exercises-videos/hip-thrust-usr1-20240523-1.mp4"
hip_thrust_usr1_20240523_2_uri = "gs://gymally-mvp/exercises-videos/hip-thrust-usr1-20240523-2.mp4"
hip_thrust_usr2_20240501_1_uri = "gs://gymally-mvp/exercises-videos/hip-thrust-usr2-20240501-1.mp4"
hip_thrust_usr2_20240523_1_uri = "gs://gymally-mvp/exercises-videos/hip-thrust-usr2-20240523-1.mp4"
hip_thrust_usr2_20240523_2_uri = "gs://gymally-mvp/exercises-videos/hip-thrust-usr2-20240523-2.mp4"
leg_press_ref_uri = "gs://gymally-mvp/exercises-videos/leg-press-ref.mp4"
leg_press_usr1_20240501_1_uri = "gs://gymally-mvp/exercises-videos/leg-press-usr1-20240501-1.mp4"
leg_press_usr1_20240523_1_uri = "gs://gymally-mvp/exercises-videos/leg-press-usr1-20240523-1.mp4"
leg_press_usr1_20240523_2_uri = "gs://gymally-mvp/exercises-videos/leg-press-usr1-20240523-2.mp4"
leg_press_usr1_20240530_1_uri = "gs://gymally-mvp/exercises-videos/leg-press-usr1-20240530-1.mp4"
unknown_usr2_20240509_1_uri = "gs://gymally-mvp/exercises-videos/unknown-exercise-usr2-20240509-1.mp4"

## Call Gemini to get a response

In [92]:
ref_video_uri = hip_thrust_ref_uri # @param: reference video URI
user_video_uri = hip_thrust_usr2_20240501_1_uri # @param: user video URI

ref_video = load_video_part(ref_video_uri)
user_video = load_video_part(user_video_uri)

In [93]:
%%time

generate()

Okay, let's break down this hip thrust! 

It looks like you're putting in the work, and that's awesome! Here's a little feedback to help you level up your hip thrust game:

**Estimated Weight:** Can't quite tell from the video, but keep pushing those limits!

* **Form (85%):**
    *  Great job keeping your chin tucked and rib cage down! 
    *  You're doing a good job stabilizing the bar with your hands.
    *  Try to focus on squeezing your glutes together even harder at the top of each rep, as if you're trying to hold a coin between your cheeks. This will help you really target those glutes!

* **Range of Movement (90%):**
    *  Your hips are getting above your knees, which is excellent! 
    *  There's a little room for improvement in achieving full hip extension at the top. Try posteriorly rotating your pelvis by slightly crunching your abs at the top.  This will help you squeeze those glutes even more!

* **Tempo (80%):**
    *  The speed on the way up looks good.  
    *  Focus 

## Compare videos (TBD, IT'S TOO SLOW NOW THAT IT DOESN'T EVEN LOAD)

In [94]:
# Display user video only - Slow
display_video_from_gcs(user_video_uri)

In [ ]:
# Compare reference and user video side by side - Too slow it doesn't even load
display_videos_from_gcs(bench_press_ref_uri, bench_press_usr3_20220501_1_uri)